In [1]:
import numpy as np
import networkx as nx
import pandas as pd
from PIL import Image
from skimage.transform import rescale
from skimage import measure as sk_measure
import itertools
import math
import time
from datetime import datetime as dt
import collections

def get_input(day, split=None, f=str.strip):
    fin = f'dat/2022-{day}.txt'
    if split is None:
        input = open(fin, 'r').readlines()
    else:
        input = open(fin, 'r').read().split(split)
    
    if f is not None:
        input = [f(x) for x in input]
    
    return input

def timestamp(ts):
    date = dt.fromtimestamp(ts)
    return f'[{date.hour:02}:{date.minute:02}:{date.second:02}]'

def output(*args, ts=0):
    out = ' '.join([str(x) for x in args])
    if ts:
        ts = timestamp(ts)
        sz = 76 - len(out) - len(ts)
        if sz > 0:
            out += ' ' * sz
        out += ts
    print(out)

def as_ints(input):    
    nums = []
    for x in input:
        x = [int(c) for c in x]
        nums.append(np.asarray(x))
    return np.asarray(nums)

# Day 1

In [2]:
input = get_input(1)

def calorie_count(data):
    lst = []
    cnt = 0
    for row in data:
        if not row:
            lst.append(cnt)
            cnt = 0
        else:
            cnt += int(row)
    return lst

cals = calorie_count(input)

output(max(cals), ts=1669870925)
output(sum(sorted(cals)[-3:]), ts=1669871038)

74198                                                             [00:02:05]
209914                                                            [00:03:58]


# Day 2

In [3]:
input = get_input(2)

score_map = {
    "A X": 4,
    "A Y": 8,
    "A Z": 3,
    "B X": 1,
    "B Y": 5,
    "B Z": 9,
    "C X": 7,
    "C Y": 2,
    "C Z": 6,
}
score_map2 = {
    "A X": 3,
    "A Y": 4,
    "A Z": 8,
    "B X": 1,
    "B Y": 5,
    "B Z": 9,
    "C X": 2,
    "C Y": 6,
    "C Z": 7,
}
        
output(sum([score_map[i] for i in input]), ts=1669958214)
output(sum([score_map2[i] for i in input]), ts=1669958383)

13484                                                             [00:16:54]
13433                                                             [00:19:43]


In [4]:
input = get_input(3)
test = [
'vJrwpWtwJgWrhcsFMMfFFhFp',
'jqHRNqRjqzjGDLGLrsFMfFZSrLrFZsSL',
'PmmdzqPrVvPwwTWBwg',
'wMqvLMZHhHMvwLHjbvcjnnSBnvTQFn',
'ttgJtRGJQctTZtZT',
'CrZsJsPPZsGzwwsLwLmpwMDw',
]

def rucksack_pairs(data):
    cnt = 0
    for row in data:
        a = row[:len(row)//2]
        b = row[len(row)//2:]
        for i in a:
            if i in b:
                val = ord(i) - 96
                if val <= 0: val += 58
                cnt += val
                break
    return cnt


output(rucksack_pairs(test))
output(rucksack_pairs(input), ts=1670044079)

def rucksack_triplets(data):
    cnt = 0
    for i in range(0, len(data), 3):
        a, b, c = data[i:i+3]
        for x in a:
            if x in b and x in c:
                val = ord(x) - 96
                if val <= 0: val += 58
                cnt += val
                break
    return cnt
        

output(rucksack_triplets(test))
output(rucksack_triplets(input), ts=1670044456)

157
7845                                                              [00:07:59]
70
2790                                                              [00:14:16]


# Day 4

In [5]:
input = get_input(4)
test = """2-4,6-8
2-3,4-5
5-7,7-9
2-8,3-7
6-6,4-6
2-6,4-8""".split('\n')

def cleanup_overlap(data, f=all):
    cnt = 0
    for row in data:
        a, b = [i.split('-') for i in row.split(',')]
        a = list(range(int(a[0]), int(a[1])+1))
        b = list(range(int(b[0]), int(b[1])+1))
        if f([i in b for i in a]) or f([i in a for i in b]):
            cnt += 1
    return cnt
        

output(cleanup_overlap(test))
output(cleanup_overlap(input), ts=1670130449)

output(cleanup_overlap(test, any))
output(cleanup_overlap(input, any), ts=1670130562)

2
424                                                               [00:07:29]
4
804                                                               [00:09:22]


# Day 5

In [6]:
input = get_input(5, split='\n', f=None)
test = """    [D]    
[N] [C]    
[Z] [M] [P]
 1   2   3 

move 1 from 2 to 1
move 3 from 1 to 3
move 2 from 2 to 1
move 1 from 1 to 2""".split('\n')

def parse_boxes(data):
    rows = []
    for row in data:
        if not row:
            break
        rows.append(row)
    
    num_cols = len(rows[-1].split())
    boxes = {i:[] for i in range(1,num_cols+1)}
    for row in rows[:-1]:
        for i in range(num_cols):
            c = row[i*4+1].strip()
            if c:
                boxes[i+1].append(c)
    return boxes

    
def move(line, boxes, use_stack=False):
    # Parse move command
    _, num, _, src, _, dst = line.split()
    src = boxes[int(src)]
    dst = boxes[int(dst)]
    
    # So we can go top to bottom using pop()
    src.reverse()
    
    # Grab all the boxes to temp stack
    stack = []
    for i in range(int(num)):
        if src:
            stack.append(src.pop())
    
    if use_stack:
        # Keep order by flipping before moving
        stack.reverse()
    
    # Move boxes to new column
    for x in stack:
        dst.insert(0, x)
    
    # Restore correct order of remaining boxes
    src.reverse()


def crane(data, stack=False):
    boxes = parse_boxes(data)
    for row in data:
        if not row.startswith('move'):
            continue
        move(row, boxes, stack)
    return "".join([x[0] for x in boxes.values()])


#output(crane(test))
#output(crane(test, True))

output(crane(input))
output(crane(input, True))

FRDSQRRCD
HRFTQVWNN


# Day 6

In [7]:
input = get_input(6)[0]
test = "mjqjpqmgbljsphdztnvjfqwrcgsmlb"
test = "bvwbjplbgvbhsrlpgdmjqwftvncz"
test = "nppdvjthqldpwncqszvftbrmjlhg"
test = "nznrnfrfntjfmvfwmzdfjlvtqnbhcprsg"
test = "zcfzfwzzqfrljwzlrfnpqdbhtmscgvjw"

def marker(data, l=4):
    for i in range(len(data)):
        marker = data[i:i+l]
        if len(set(marker)) == l:
            return i+l

#output(marker(test, 14))
output(marker(input), ts=1670303053)
output(marker(input, 14), ts=1670303133)

1531                                                              [00:04:13]
2518                                                              [00:05:33]


# Day 7

In [8]:
input = get_input(7)
test = """$ cd /
$ ls
dir a
14848514 b.txt
8504156 c.dat
dir d
$ cd a
$ ls
dir e
29116 f
2557 g
62596 h.lst
$ cd e
$ ls
584 i
$ cd ..
$ cd ..
$ cd d
$ ls
4060174 j
8033020 d.log
5626152 d.ext
7214296 k""".split('\n')

class Dir(object):
    def __init__(self, name, d):
        self.name = name
        self.dirs = []
        self.size = 0
        self.parent = d
    def __repr__(self):
        return f"{self.name}: {self.size} - {self.dirs}"

def du(cur_dir):
    size = cur_dir.size
    #print(cur_dir.name, size)
    for d in cur_dir.dirs:
        size += du(d)
        #print(cur_dir.name, size)
    cur_dir.size = size
    return size

def pr(cur_dir, lvl=0):
    print('- '*(lvl+1), cur_dir.name, cur_dir.size)
    for d in cur_dir.dirs:
        pr(d, lvl+1)
        
def walk(cur_dir):
    size = 0
    if cur_dir.size <= 100000:
        size += cur_dir.size
    for d in cur_dir.dirs:
        size += walk(d)
    return size

def walk2(cur_dir, need, size):
    if cur_dir.size > need and cur_dir.size < size:
        size = cur_dir.size
    for d in cur_dir.dirs:
        size = walk2(d, need, size)
    return size    

def sum_dirs(data):
    cur_dir = None
    for row in data:
        if row.startswith("$ cd"):
            d = row.split()[2]
            if d == "..":
                cur_dir = cur_dir.parent
            else:
                cur_dir = Dir(d, cur_dir)
                if cur_dir.parent is not None:
                    cur_dir.parent.dirs.append(cur_dir)
        elif row.startswith("$ ls"):
            continue
        elif row.startswith("dir"):
            continue
        else:
            cur_dir.size += int(row.split()[0])
    
    while cur_dir.parent is not None:
        cur_dir = cur_dir.parent
    
    du(cur_dir)
    return cur_dir
    
test_root = sum_dirs(test)
root = sum_dirs(input)
#output(walk(test_root))
output(walk(root), ts=1670395101)
    
def delete(root):
    total = 70000000
    need = 30000000
    free = total - root.size
    min_del = need - free
    #print(total, need, free, min_del)
    return walk2(root, min_del, total)

#output(delete(test_root))
output(delete(root), ts=1670396117)

1449447                                                           [01:38:21]
8679207                                                           [01:55:17]


# Day 8

In [9]:
input = as_ints(get_input(8))
test = """30373
25512
65332
33549
35390""".split('\n')
test = as_ints(test)

def visible(data):
    cnt = 0
    for y in range(1, data.shape[0]-1):
        for x in range(1, data.shape[1]-1):
            if data[y,x] > min(np.max(data[:y,x]), np.max(data[y+1:,x]), np.max(data[y,:x]), np.max(data[y,x+1:])):
                cnt += 1
    return cnt + data.shape[0]*2 + data.shape[1] * 2 - 4

output(visible(test))
output(visible(input), ts=1670476923)

def scenic(data):
    score = 0
    for y in range(1, data.shape[0]-1):
        for x in range(1, data.shape[1]-1):
            i = data[y,x]
            n = s = e = w = 0
            for x0 in range(x-1, -1, -1):
                w += 1
                if data[y,x0] >= i:
                    break
            for x0 in range(x+1, data.shape[1]):
                e += 1
                if data[y,x0] >= i:
                    break
            for y0 in range(y-1, -1, -1):
                n += 1
                if data[y0,x] >= i:
                    break
            for y0 in range(y+1, data.shape[0]):
                s += 1
                if data[y0,x] >= i:
                    break
            #print(x,y,n,s,e,w,score)
            score = max(score, n*s*e*w)
    return score

output(scenic(test))
output(scenic(input), ts=1670477460)

21
1533                                                              [00:22:03]
8
345744                                                            [00:31:00]


# Day 9

In [10]:
input = get_input(9)
test = """R 4
U 4
L 3
D 1
R 4
D 1
L 5
R 2""".split('\n')

def move_tail(head, tail):
    xh, yh = head
    xt, yt = tail
    
    dx = xh-xt
    ddx = dx // abs(dx) if dx != 0 else 0
    dy = yh-yt
    ddy = dy // abs(dy) if dy != 0 else 0
    
    if abs(dx) > 1:
        xt += ddx
        if dy != 0:
            yt += ddy
    elif abs(dy) > 1:
        yt += ddy
        if dx != 0:
            xt += ddx
    
    return xt, yt

move_head = lambda x,y,d: {"U": (x,y-1), "D": (x,y+1), "L": (x-1,y), "R": (x+1,y)}[d]

def rope(data, k=1):
    a = np.zeros((1000,1000))
    xh = yh = 500
    knots = [(500,500)] * k
    for row in data:
        d, n = row.split()
        for i in range(int(n)):
            xh, yh = move_head(xh, yh, d)
            for i in range(k):
                tail = knots[i]
                if i == 0:
                    head = (xh, yh)
                else:
                    head = knots[i-1]
                knots[i] = move_tail(head, tail)
            a[knots[-1][1]][knots[-1][0]] += 1
    return np.count_nonzero(a)

#output(rope(test))
output(rope(input), ts=1670563702)
output(rope(input, 9), ts=1670564122)

6067                                                              [00:28:22]
2471                                                              [00:35:22]


# Day 10

In [11]:
input = get_input(10)
test = """addx 15
addx -11
addx 6
addx -3
addx 5
addx -1
addx -8
addx 13
addx 4
noop
addx -1
addx 5
addx -1
addx 5
addx -1
addx 5
addx -1
addx 5
addx -1
addx -35
addx 1
addx 24
addx -19
addx 1
addx 16
addx -11
noop
noop
addx 21
addx -15
noop
noop
addx -3
addx 9
addx 1
addx -3
addx 8
addx 1
addx 5
noop
noop
noop
noop
noop
addx -36
noop
addx 1
addx 7
noop
noop
noop
addx 2
addx 6
noop
noop
noop
noop
noop
addx 1
noop
noop
addx 7
addx 1
noop
addx -13
addx 13
addx 7
noop
addx 1
addx -33
noop
noop
noop
addx 2
noop
noop
noop
addx 8
noop
addx -1
addx 2
addx 1
noop
addx 17
addx -9
addx 1
addx 1
addx -3
addx 11
noop
noop
addx 1
noop
addx 1
noop
noop
addx -13
addx -19
addx 1
addx 3
addx 26
addx -30
addx 12
addx -1
addx 3
addx 1
noop
noop
noop
addx -9
addx 18
addx 1
addx 2
noop
noop
addx 9
noop
noop
noop
addx -1
addx 2
addx -37
addx 1
addx 3
noop
addx 15
addx -21
addx 22
addx -6
addx 1
noop
addx 2
addx 1
noop
addx -10
noop
noop
addx 20
addx 1
addx 2
addx 2
addx -6
addx -11
noop
noop
noop""".split('\n')

def power(c, x, out):
    if out is None:
        out = 0
    if c in [20, 60, 100, 140, 180, 220]:
            out += c * x
    return out

def sprite(c, x, out):
    if out is None:
        out = ""
    c = c % 40
    if c == 0:
        out += '\n'
    if c in [x,x+1,x-1]:
        out += '#'
    else:
        out += '.'
    return out

def cathode(data, f):
    x = 1
    i = 0
    cycle = 0
    out = None
    while cycle < 240:
        out = f(cycle, x, out)
        row = data[i]
        if row == 'noop':
            cycle += 1
        else:            
            _, n = row.split()
            cycle += 1
            out = f(cycle, x, out)
            cycle += 1
            x += int(n)
        i += 1
    return out

output(cathode(test, power))
output(cathode(input, power), ts=1670649240)

output(cathode(test, sprite))
output(cathode(input, sprite), ts=1670649894)

13360
14760                                                             [00:14:00]

##..##..##..##..##..##..##..##..##..##..
###...###...###...###...###...###...###.
####....####....####....####....####....
#####.....#####.....#####.....#####.....
######......######......######......####
#######.......#######.......#######.....

####.###...##..###..#....####.####.#..#.
...#.#..#.#..#.#..#.#....#.......#.#..#.
..#..#..#.#..#.#..#.#....###....#..#..#.
.#...###..####.###..#....#.....#...#..#.
#....#.#..#..#.#.#..#....#....#....#..#.
####.#..#.#..#.#..#.####.#....####..##..[00:24:54]


# Day 11

In [31]:
input = get_input(11)
test = """Monkey 0:
  Starting items: 79, 98
  Operation: new = old * 19
  Test: divisible by 23
    If true: throw to monkey 2
    If false: throw to monkey 3

Monkey 1:
  Starting items: 54, 65, 75, 74
  Operation: new = old + 6
  Test: divisible by 19
    If true: throw to monkey 2
    If false: throw to monkey 0

Monkey 2:
  Starting items: 79, 60, 97
  Operation: new = old * old
  Test: divisible by 13
    If true: throw to monkey 1
    If false: throw to monkey 3

Monkey 3:
  Starting items: 74
  Operation: new = old + 3
  Test: divisible by 17
    If true: throw to monkey 0
    If false: throw to monkey 1""".split('\n')

class Monkey(object):
    def __init__(self, num, items, op, test, true, false):
        self.num = num
        self.items = items
        self.test = test
        self.true = true
        self.false = false
        self.count = 0
        _, _, _, o, n = op.split()
        if o == '+':
            self.op = lambda x: x + int(n)
        elif o == '*':
            if n == 'old':
                self.op = lambda x: x**2
            else:
                self.op = lambda x: x * int(n)
            
    
    def turn(self, monkeys, limit=0):
        while self.items:
            x = self.items.pop()
            self.count += 1
            x = self.op(x)
            if limit == 0:
                x = x // 3
            elif x > limit:
                x = limit + (x % limit)
            if x % self.test == 0:
                monkeys[self.true].items.append(x)
            else:
                monkeys[self.false].items.append(x)
            
def monkey_business(data, rounds, use_limit=False):
    i = 0
    monkeys = {}
    while i < len(data):
        monkey = int(data[i].split()[1][:-1])
        items = [int(x) for x in data[i+1].split(':')[1].split(',')]
        op = data[i+2].split(':')[1]
        test = int(data[i+3].split()[-1])
        true = int(data[i+4].split()[-1])
        false = int(data[i+5].split()[-1])
        monkeys[monkey] = Monkey(monkey, items, op, test, true, false)
        i += 7    
    
    if use_limit:
        limit = int(np.product([m.test for m in monkeys.values()]))
    else:
        limit = 0
    
    for i in range(rounds):
        for j in range(len(monkeys)):
            monkeys[j].turn(monkeys, limit)
    
    counts = [monkeys[k].count for k in monkeys]
    counts.sort()
    return counts[-1] * counts[-2]

output(monkey_business(test, 20))
output(monkey_business(input, 20), ts=1670736195)

output(monkey_business(test, 10000, True))
output(monkey_business(input, 10000, True))

10605
58786                                                             [00:23:15]
2713310158
14952185856                                                       [19:07:15]


# Day 12

In [32]:
input = get_input(12)
test = """Sabqponm
abcryxxl
accszExk
acctuvwj
abdefghi""".split('\n')

def find_point(data, c):
    for y in range(len(data)):
        for x in range(len(data[y])):
            if data[y][x] == c:
                return x, y

def find_route(start, target, steps, grid):
    best = {}
    q = [(steps, start[0], start[1])]
    while q:
        q = sorted(q, key = lambda x: x[0])
        steps, x, y = q.pop(0)
        if (x,y) in best and best[(x,y)] <= steps:
            continue
        best[(x,y)] = min(best[(x,y)] if (x,y) in best else steps, steps)
        if (x,y) == target:
            return best[(x,y)]
        for a, b in [coord for coord in ((x,y+1), (x-1,y), (x+1,y), (x,y-1)) if coord in grid]:
            if grid[(a,b)] <= grid[(x,y)] + 1:
                #print(f"{x},{y} ({chr(grid[(x,y)])}) => {a},{b} ({chr(grid[(a,b)])}) ({steps+1})")
                q.append((steps + 1, a, b))
                
def climb(data, start, end):
    data = [[ord(x) for x in y] for y in data]
    grid = {(x,y) : data[y][x] for x in range(len(data[0])) for y in range(len(data))}

    grid[start] = ord('a')
    grid[end] = ord('z')

    return find_route(start, end, 0, grid)

def part_one(data):
    start = find_point(data, 'S')
    end = find_point(data, 'E')
    return climb(data, start, end)

output(part_one(test))
output(part_one(input), ts=1670822974)

def find_shortest(data):
    data = [x.replace('S', 'a') for x in data]
    end = find_point(data, 'E')
    shortest = 999
    for y in range(len(data)):
        for x in range(len(data[y])):
            if data[y][x] == 'a':
                s = climb(data, (x,y), end)
                if s:
                    shortest = min(shortest, s)
    return shortest

output(find_shortest(test))
output(find_shortest(input), ts=1670824031)

31
462                                                               [00:29:34]
29
451                                                               [00:47:11]


# Day 13

In [30]:
input = get_input(13)
test = """[1,1,3,1,1]
[1,1,5,1,1]

[[1],[2,3,4]]
[[1],4]

[9]
[[8,7,6]]

[[4,4],4,4]
[[4,4],4,4,4]

[7,7,7,7]
[7,7,7]

[]
[3]

[[[]]]
[[]]

[1,[2,[3,[4,[5,6,7]]]],8,9]
[1,[2,[3,[4,[5,6,0]]]],8,9]""".split('\n')

def compare(a,b):
    if a == b:
        return 0
    
    if type(a) == type(b) and isinstance(a,int):
        if a < b:
            return -1
        return 1
    
    if type(a) != type(b):
        if isinstance(a, list):
            return compare(a, [b])
        else:
            return compare([a], b)
    
    for a0,b0 in zip(a,b):
        c = compare(a0, b0)
        if c == 0:
            continue
        return c
    
    if len(a) <= len(b):
        return -1
    return 1

def part_one(data):
    i = idx = sum_idx = 0
    while i < len(data):
        idx += 1
        a = eval(data[i])
        b = eval(data[i+1])
        i += 3
        #print(idx,a,b,compare(a,b))
        #if idx != 134:continue
        if compare(a,b) <= 0:
            #print(idx,True)
            sum_idx += idx
        else:
            pass
            #print(idx,False)
            #print()
            #print()
        
        
    return sum_idx

output(part_one(test))
output(part_one(input))

from functools import cmp_to_key

def part_two(data):
    i = idx = sum_idx = 0
    packs = []
    while i < len(data):
        idx += 1
        packs.append(eval(data[i]))
        packs.append(eval(data[i+1]))
        i += 3
    packs.append([[2]])
    packs.append([[6]])
    packs.sort(key=cmp_to_key(compare))
    return (packs.index([[2]])+1) * (packs.index([[6]])+1)

output(part_two(test))
output(part_two(input))

13
5625
140
23111


# Day 14

In [31]:
input = get_input(14)
test = """498,4 -> 498,6 -> 496,6
503,4 -> 502,4 -> 502,9 -> 494,9""".split('\n')

def parse_grid(data, inf):
    x0 = y0 = 9999999
    x1 = y1 = 0
    for row in data:
        nums = [eval(f"({x})") for x in row.split() if not x == '->']
        x0 = min(x0, min([x[0] for x in nums]))
        y0 = min(x0, min([x[1] for x in nums]))
        x1 = max(x1, max([x[0] for x in nums]))
        y1 = max(y1, max([x[1] for x in nums]))
    #print(x0,y0,x1,y1)
    
    if inf:
        grid = {(x,y):0 for x in range(x0 * -5, x1 * 5) for y in range(0,y1+3)}
    else:
        grid = {(x,y):0 for x in range(x0, x1+1) for y in range(0,y1+1)}
        
    for row in data:
        nums = [eval(f"({x})") for x in row.split() if not x == '->']
        for i in range(len(nums)-1):
            a = nums[i]
            b = nums[i+1]
            X = (a[0],b[0])
            Y = (a[1],b[1])
            #print(a,b)
            for x in range(min(X), max(X)+1):
                for y in range(min(Y), max(Y)+1):
                    #print(x,y)
                    grid[(x,y)] = 1
    if inf:
        for x in range(x0 * -5, x1 * 5):
            grid[(x,y1+2)] = 1
    
    #for y in range(0,y1+3):
    #for y in range(0,y1+1):
    #    s=''
    #    #for x in range(x0-10,x1+10):
    #    for x in range(x0,x1+1):
    #        s += str(grid[(x,y)])
    #    print(s)
            
    return grid

def sand(grid, inf):
    x = 500
    y = 0
    while (x,y) in grid and grid[(x,y)] == 0:
        if (x,y+1) not in grid or grid[(x,y+1)] == 0:
            y += 1
        elif (x-1,y+1) not in grid or grid[(x-1,y+1)] == 0:
            x -= 1
            y += 1
        elif (x+1,y+1) not in grid or grid[(x+1,y+1)] == 0:
            x += 1
            y += 1
        else:
            grid[(x,y)] = 1
    
    if inf:
        return grid[(500,0)] == 0
    else:
        return (x,y) in grid
        

def waterfall(data, inf=False):
    grid = parse_grid(data, inf)
    count = 0
    while True:
        if not sand(grid, inf):
            break
        count += 1
    if inf:
        count += 1
        
    return count

output(waterfall(test))
output(waterfall(input), ts=1670995757)

output(waterfall(test, True))
output(waterfall(input, True), ts=1670996307)

24
843                                                               [00:29:17]
93
27625                                                             [00:38:27]


# Day 15

In [3]:
input = get_input(15)
test = """Sensor at x=2, y=18: closest beacon is at x=-2, y=15
Sensor at x=9, y=16: closest beacon is at x=10, y=16
Sensor at x=13, y=2: closest beacon is at x=15, y=3
Sensor at x=12, y=14: closest beacon is at x=10, y=16
Sensor at x=10, y=20: closest beacon is at x=10, y=16
Sensor at x=14, y=17: closest beacon is at x=10, y=16
Sensor at x=8, y=7: closest beacon is at x=2, y=10
Sensor at x=2, y=0: closest beacon is at x=2, y=10
Sensor at x=0, y=11: closest beacon is at x=2, y=10
Sensor at x=20, y=14: closest beacon is at x=25, y=17
Sensor at x=17, y=20: closest beacon is at x=21, y=22
Sensor at x=16, y=7: closest beacon is at x=15, y=3
Sensor at x=14, y=3: closest beacon is at x=15, y=3
Sensor at x=20, y=1: closest beacon is at x=15, y=3""".split('\n')

def part_one(data, y0):
    grid = {}
    for row in data:
        row = row.split()
        sx = int(row[2][2:-1])
        sy = int(row[3][2:-1])
        bx = int(row[8][2:-1])
        by = int(row[9][2:])
        
        dist = abs(sx-bx) + abs(sy-by)
        grid[(sx,sy)] = 1
        grid[(bx,by)] = 2
        print(sx,sy,bx,by,dist)
        
        y=y0
        for x in range(sx-dist,sx+dist+1):
            if abs(sx-x) + abs(sy-y) > dist: continue
            if (x,y) not in grid:
                grid[(x,y)] = -1

    for y in range(20):
        s = ''
        for x in range(20):
            if (x,y) in grid:
                c = grid[(x,y)]
                if c == -1:
                    s += '#'
                elif c == 1:
                    s += 'S'
                elif c == 2:
                    s += 'B'
            else:
                s += '.'
        print(s)
    
    return [grid[(x,y)] for x,y in grid if y == y0].count(-1)

#output(part_one(test, 10))
#output(part_one(input, 2000000))

def part_two(data, lim):
    coords = []
    for row in data:
        row = row.split()
        sx = int(row[2][2:-1])
        sy = int(row[3][2:-1])
        bx = int(row[8][2:-1])
        by = int(row[9][2:])
        
        dist = abs(sx-bx) + abs(sy-by)
        coords.append((sx,sy,dist))
    
    y0 = 3250000 if lim > 20 else 0
    for y in range(y0,lim+1):
        if y % 10000 == 0:print("Row",y)
        x = 0
        while x < lim+1:
            for c in coords:
                x0,y0,d = c
                if abs(x0-x) + abs(y0-y) <= d:
                    x += d - abs(x0-x) - abs(y0-y)
                    break
            else:
                return x * 4000000 + y
            x += 1
    
output(part_two(test, 20))
output(part_two(input, 4000000))

Row 0
56000011
Row 3250000
10826395253551


# Day 16

In [11]:
input = get_input(16)
test = """Valve AA has flow rate=0; tunnels lead to valves DD, II, BB
Valve BB has flow rate=13; tunnels lead to valves CC, AA
Valve CC has flow rate=2; tunnels lead to valves DD, BB
Valve DD has flow rate=20; tunnels lead to valves CC, AA, EE
Valve EE has flow rate=3; tunnels lead to valves FF, DD
Valve FF has flow rate=0; tunnels lead to valves EE, GG
Valve GG has flow rate=0; tunnels lead to valves FF, HH
Valve HH has flow rate=22; tunnel leads to valve GG
Valve II has flow rate=0; tunnels lead to valves AA, JJ
Valve JJ has flow rate=21; tunnel leads to valve II""".split('\n')

class Valve(object):
    def __init__(self, line):
        line = line.replace(',', '').split()
        self.name = line[1]
        rate = line[4]
        self.rate = int(rate[5:-1])
        self.tunnels = line[9:]
        self.open = False
        print(f"Valve {self.name} @ rate {self.rate} => {self.tunnels}")

def get_scores(g, m, cur):
    scores = []
    for n in g:
        if g.nodes[n]['rate'] == 0 or not g.nodes[n]['closed']:
            continue
        
        cost = nx.shortest_path_length(g, cur, n) + 1
        if cost <= m:
            score = g.nodes[n]['rate'] * (m - cost)
            scores.append((n, score, m-cost))
            
    return scores
    
def find_path(g, m, pth, pres):
    if m <= 0:
        return pth, pres
    
    opts = get_scores(g, m, pth[-1])
    best = (pth,pres)
    for node, score, m2 in opts:
        if score <= 0: continue
        g2 = g.copy()
        g2.nodes[node]['closed'] = False
        a, b = find_path(g2, m2, pth + [node], pres+score)
        #print(f"{pth[-1]} => {node} @ {score} ({m2})")
        #print(a,b)
        if b > best[1]:
            best = (a, b)
    
    #print(best)
    return best
    
    
def part_one(data):
    g = nx.Graph()
    for row in data:
        v = Valve(row)
        g.add_node(v.name, rate=v.rate, closed=True)
        for t in v.tunnels:
            g.add_edge(v.name, t)
    
    return find_path(g, 30, ['AA'], 0)
        

#output(part_one(test))
#output(part_one(input))

def find_path2(g, m1, m2, pth1, pth2, pres):
    if m1 <= 0 and m2 <= 0:
        return pth1, pth2, pres
    
    opts1 = get_scores(g, m1, pth1[-1])
    best1 = (pth1,pres)
    for node, score, m3 in opts1:
        if score <= 0: continue
        g2 = g.copy()
        g2.nodes[node]['closed'] = False
        a, b, c = find_path2(g2, m3, m2, pth1 + [node], pth2, pres+score)
        #print(f"{pth[-1]} => {node} @ {score} ({m2})")
        #print(a,b)
        if c > best1[1]:
            best1 = (a, c)
    
    opts2 = get_scores(g, m2, pth2[-1])
    best2 = (pth2,pres)
    for node, score, m3 in opts2:
        if score <= 0: continue
        g2 = g.copy()
        g2.nodes[node]['closed'] = False
        a, b, c = find_path2(g2, m1, m3, pth1, pth2 + [node], pres+score)
        #print(f"{pth[-1]} => {node} @ {score} ({m2})")
        #print(a,b)
        if c > best2[1]:
            best2 = (b, c)
    
    #print(best)
    return best1[0], best2[0], best1[1] + best2[1]

def part_two(data):
    g = nx.Graph()
    for row in data:
        v = Valve(row)
        g.add_node(v.name, rate=v.rate, closed=True)
        for t in v.tunnels:
            g.add_edge(v.name, t)
    
    return find_path2(g, 26, 26, ['AA'], ['AA'], 0)

output(part_two(test))

Valve AA @ rate 0 => ['DD', 'II', 'BB']
Valve BB @ rate 13 => ['CC', 'AA']
Valve CC @ rate 2 => ['DD', 'BB']
Valve DD @ rate 20 => ['CC', 'AA', 'EE']
Valve EE @ rate 3 => ['FF', 'DD']
Valve FF @ rate 0 => ['EE', 'GG']
Valve GG @ rate 0 => ['FF', 'HH']
Valve HH @ rate 22 => ['GG']
Valve II @ rate 0 => ['AA', 'JJ']
Valve JJ @ rate 21 => ['II']
(['AA', 'DD', 'HH', 'EE', 'CC', 'BB', 'JJ'], ['AA', 'DD', 'HH', 'EE', 'CC', 'BB', 'JJ'], 212756)


# Day 17

In [41]:
input = get_input(17)[0]
test = """>>><<><>><<<>><>>><<<>>><<<><<<>><>><<>>"""

rocks = [
    [[1,1,1,1]],
    [[0,1,0],[1,1,1],[0,1,0]],
    [[0,0,1],[0,0,1],[1,1,1]],
    [[1],[1],[1],[1]],
    [[1,1],[1,1]]
]

def collide(rock, cave, y0,y1,x0,x1):
    #print(x0,x1,y0,y1,rock.shape, cave[y0:y1,x0:x1].shape)
    return np.max(rock + cave[y0:y1,x0:x1]) > 1

def collide_down(rock, cave, x0, y):
    h,w = rock.shape
    return collide(rock, cave, y-h+1,y+1,x0,x0+w)
def collide_left(rock, cave, x0, y):
    h,w = rock.shape
    return x0 == 0 or collide(rock, cave, y-h,y,x0-1,x0+w-1)
def collide_right(rock, cave, x0, y):
    h,w = rock.shape
    return x0+w == 7 or collide(rock, cave, y-h,y,x0+1,x0+w+1)

def blow(x0, x1, y, d, rock, cave):
    left = d == '<'
    #print(x0,x1,y,h,left)
    if left and not collide_left(rock, cave, x0, y):
        return x0-1, x1-1
    elif not left and not collide_right(rock, cave, x0, y):
        return x0+1, x1+1
    return x0, x1

def foo(data, lim=2022):
    r = 0
    j = 0
    k = len(data)
    #cave = np.zeros((4 * lim + 6, 7), np.byte)
    cave = np.zeros((10000, 7), np.byte)
    h0,w0 = cave.shape
    cave[h0-1,:] = 1
    
    for i in range(lim):
        h = min(np.where(cave>0)[0])
        if h < 5000:
            h0 += 2500
            print(i,h0, dt.now())
            cave[7500:,:] = cave[5000:7500,:]
            cave[5000:7500,:] = cave[2500:5000,:]
            cave[2500:5000,:] = cave[:2500,:]
            h = min(np.where(cave>0)[0])
        rock = np.asarray(rocks[i % len(rocks)], np.byte)
        rh, rw = rock.shape
        x0 = 2
        x1 = x0 + rw - 1
        y = h - 3
        for ii in range(3):
            left = data[j%k] == '<'
            if left and x0 != 0:
                x0 -= 1
                x1 -= 1
            elif not left and x1 != 6:
                x0 += 1
                x1 += 1
            j += 1
        y = h
        while True:
            x0, x1 = blow(x0, x1, y, data[j%k], rock, cave)
            j += 1
            if collide_down(rock, cave, x0, y):
                break
            y += 1
        
        #print(x0,x1,y,h)
        #print(collide(rock, cave, x0, y))
        cave[y-rh:y,x0:x0+rw][np.where(rock==1)] = 1
        #print(h0 - min(np.where(cave>0)[0]) - 1)
        #print(cave[h0-20:,:])
        
    return h0 - min(np.where(cave>0)[0]) - 1

def bar(data, lim=2022):
    r = 0
    j = 0
    k = len(data)
    
    #cave = np.zeros((4 * lim + 6, 7), np.byte)
    cave = np.zeros((10000, 7), np.byte)
    #cave = np.zeros((4 * k + 6, 7), np.byte)
    h0,w0 = cave.shape
    cave[h0-1,:] = 1
    
    loop = []
    for i in range(lim):
        h = min(np.where(cave>0)[0])
        if h < 5000:
            h0 += 2500
            print(i,h0, dt.now())
            cave[7500:,:] = cave[5000:7500,:]
            cave[5000:7500,:] = cave[2500:5000,:]
            cave[2500:5000,:] = cave[:2500,:]
            h = min(np.where(cave>0)[0])
        rock = np.asarray(rocks[i % len(rocks)], np.byte)
        rh, rw = rock.shape
        x0 = 2
        x1 = x0 + rw - 1
        y = h - 3
        for ii in range(3):
            left = data[j%k] == '<'
            if left and x0 != 0:
                x0 -= 1
                x1 -= 1
            elif not left and x1 != 6:
                x0 += 1
                x1 += 1
            j += 1
        y = h
        while True:
            x0, x1 = blow(x0, x1, y, data[j%k], rock, cave)
            j += 1
            if collide_down(rock, cave, x0, y):
                break
            y += 1
        
        cave[y-rh:y,x0:x0+rw][np.where(rock==1)] = 1
        if i < k:
            loop.append(h0 - min(np.where(cave>0)[0]) - 1)
    
    print(cave[-10:,:],'\n\n',cave[-k-10:-k+5,:])
    #return h0 - min(np.where(cave>0)[0]) - 1, lim//k*loop[-1]+loop[lim%k],lim//k,lim%k,loop[-1],loop[lim%k-1]
    

output(foo(test))
#output(foo(input))
#output(foo(test,1000000000000))
output(bar(test))
#output(bar(input))
output(foo(test,50),bar(test,50))
output(foo(test,500),bar(test,500))

3068
[[0 0 0 0 1 1 0]
 [0 0 0 0 1 1 0]
 [0 0 0 0 1 0 0]
 [0 0 1 0 1 0 0]
 [0 0 1 0 1 0 0]
 [1 1 1 1 1 0 0]
 [0 0 1 1 1 0 0]
 [0 0 0 1 0 0 0]
 [0 0 1 1 1 1 0]
 [1 1 1 1 1 1 1]] 

 [[1 0 1 0 0 0 0]
 [1 0 1 0 0 0 0]
 [1 1 1 1 0 0 0]
 [0 0 1 1 1 1 1]
 [0 0 0 1 0 1 1]
 [0 0 1 1 1 1 0]
 [0 1 1 0 0 0 0]
 [0 1 1 0 0 0 1]
 [0 0 1 0 0 0 1]
 [0 0 1 0 1 1 1]
 [0 0 1 0 0 1 0]
 [0 0 1 0 1 1 1]
 [0 1 1 1 1 1 0]
 [0 0 0 0 1 0 0]
 [0 0 0 0 1 0 0]]
None
[[0 0 0 0 1 1 0]
 [0 0 0 0 1 1 0]
 [0 0 0 0 1 0 0]
 [0 0 1 0 1 0 0]
 [0 0 1 0 1 0 0]
 [1 1 1 1 1 0 0]
 [0 0 1 1 1 0 0]
 [0 0 0 1 0 0 0]
 [0 0 1 1 1 1 0]
 [1 1 1 1 1 1 1]] 

 [[1 0 1 0 0 0 0]
 [1 0 1 0 0 0 0]
 [1 1 1 1 0 0 0]
 [0 0 1 1 1 1 1]
 [0 0 0 1 0 1 1]
 [0 0 1 1 1 1 0]
 [0 1 1 0 0 0 0]
 [0 1 1 0 0 0 1]
 [0 0 1 0 0 0 1]
 [0 0 1 0 1 1 1]
 [0 0 1 0 0 1 0]
 [0 0 1 0 1 1 1]
 [0 1 1 1 1 1 0]
 [0 0 0 0 1 0 0]
 [0 0 0 0 1 0 0]]
78 None
[[0 0 0 0 1 1 0]
 [0 0 0 0 1 1 0]
 [0 0 0 0 1 0 0]
 [0 0 1 0 1 0 0]
 [0 0 1 0 1 0 0]
 [1 1 1 1 1 0 0]
 [0 0 1 1 1 0 0]
 [0

# Day 18

In [64]:
input = get_input(18)
test = """2,2,2
1,2,2
3,2,2
2,1,2
2,3,2
2,2,1
2,2,3
2,2,4
2,2,6
1,2,5
3,2,5
2,1,5
2,3,5""".split('\n')

def is_pocket(a):
    a.sort()
    return a[-1] - a[0] == 1 and a[1] == a[2] == a[3] == a[4]

def foo(data, ext_only=False):
    cubes = []
    for row in data:
        cubes.append([int(i) for i in row.split(',')])
    
    count = len(cubes) * 6
    for i in range(len(cubes)):
        a = cubes[i]
        for j in range(len(cubes)):
            if i == j: continue
            b = cubes[j]
            for k in range(3):
                if a[k] == b[k] and a[(k+1)%3] == b[(k+1)%3] and abs(a[(k+2)%3]-b[(k+2)%3]) == 1:
                    count -= 1
        
            if ext_only:
                for k in range(len(cubes)):
                    if k in [i,j]: continue
                    c = cubes[k]
                    for l in range(len(cubes)):
                        if l in [i,j,k]: continue
                        d = cubes[l]
                        for m in range(len(cubes)):
                            if m in [i,j,k,l]: continue
                            e = cubes[m]
                            for n in range(len(cubes)):
                                if n in [i,j,k,l,m]: continue
                                f = cubes[n]
                                
                                cube = [a,b,c,d,e,f]
                                x = [el[0] for el in cube]
                                y = [el[1] for el in cube]
                                z = [el[2] for el in cube]
                                if all([is_pocket for ii in [x,y,z]]):
                                    print("PCKET",i,j,k,l,m,n,cube)
                                
                        
                        
            
        
    return count

output(foo(test))
output(foo(input))
output(foo(test, True))
#output(foo(input, True))

64
3396
PCKET 0 1 2 3 4 5 [[2, 2, 2], [1, 2, 2], [3, 2, 2], [2, 1, 2], [2, 3, 2], [2, 2, 1]]
PCKET 0 1 2 3 4 6 [[2, 2, 2], [1, 2, 2], [3, 2, 2], [2, 1, 2], [2, 3, 2], [2, 2, 3]]
PCKET 0 1 2 3 4 7 [[2, 2, 2], [1, 2, 2], [3, 2, 2], [2, 1, 2], [2, 3, 2], [2, 2, 4]]
PCKET 0 1 2 3 4 8 [[2, 2, 2], [1, 2, 2], [3, 2, 2], [2, 1, 2], [2, 3, 2], [2, 2, 6]]
PCKET 0 1 2 3 4 9 [[2, 2, 2], [1, 2, 2], [3, 2, 2], [2, 1, 2], [2, 3, 2], [1, 2, 5]]
PCKET 0 1 2 3 4 10 [[2, 2, 2], [1, 2, 2], [3, 2, 2], [2, 1, 2], [2, 3, 2], [3, 2, 5]]
PCKET 0 1 2 3 4 11 [[2, 2, 2], [1, 2, 2], [3, 2, 2], [2, 1, 2], [2, 3, 2], [2, 1, 5]]
PCKET 0 1 2 3 4 12 [[2, 2, 2], [1, 2, 2], [3, 2, 2], [2, 1, 2], [2, 3, 2], [2, 3, 5]]
PCKET 0 1 2 3 5 4 [[2, 2, 2], [1, 2, 2], [3, 2, 2], [2, 1, 2], [2, 2, 1], [2, 3, 2]]
PCKET 0 1 2 3 5 6 [[2, 2, 2], [1, 2, 2], [3, 2, 2], [2, 1, 2], [2, 2, 1], [2, 2, 3]]
PCKET 0 1 2 3 5 7 [[2, 2, 2], [1, 2, 2], [3, 2, 2], [2, 1, 2], [2, 2, 1], [2, 2, 4]]
PCKET 0 1 2 3 5 8 [[2, 2, 2], [1, 2, 2], [3, 2, 2], [2

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



 9 10 11 [[2, 1, 2], [2, 2, 6], [2, 2, 1], [1, 2, 5], [3, 2, 5], [2, 1, 5]]
PCKET 3 8 5 9 10 12 [[2, 1, 2], [2, 2, 6], [2, 2, 1], [1, 2, 5], [3, 2, 5], [2, 3, 5]]
PCKET 3 8 5 9 11 0 [[2, 1, 2], [2, 2, 6], [2, 2, 1], [1, 2, 5], [2, 1, 5], [2, 2, 2]]
PCKET 3 8 5 9 11 1 [[2, 1, 2], [2, 2, 6], [2, 2, 1], [1, 2, 5], [2, 1, 5], [1, 2, 2]]
PCKET 3 8 5 9 11 2 [[2, 1, 2], [2, 2, 6], [2, 2, 1], [1, 2, 5], [2, 1, 5], [3, 2, 2]]
PCKET 3 8 5 9 11 4 [[2, 1, 2], [2, 2, 6], [2, 2, 1], [1, 2, 5], [2, 1, 5], [2, 3, 2]]
PCKET 3 8 5 9 11 6 [[2, 1, 2], [2, 2, 6], [2, 2, 1], [1, 2, 5], [2, 1, 5], [2, 2, 3]]
PCKET 3 8 5 9 11 7 [[2, 1, 2], [2, 2, 6], [2, 2, 1], [1, 2, 5], [2, 1, 5], [2, 2, 4]]
PCKET 3 8 5 9 11 10 [[2, 1, 2], [2, 2, 6], [2, 2, 1], [1, 2, 5], [2, 1, 5], [3, 2, 5]]
PCKET 3 8 5 9 11 12 [[2, 1, 2], [2, 2, 6], [2, 2, 1], [1, 2, 5], [2, 1, 5], [2, 3, 5]]
PCKET 3 8 5 9 12 0 [[2, 1, 2], [2, 2, 6], [2, 2, 1], [1, 2, 5], [2, 3, 5], [2, 2, 2]]
PCKET 3 8 5 9 12 1 [[2, 1, 2], [2, 2, 6], [2, 2, 1], [1, 2, 5

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



 12 [[2, 2, 4], [1, 2, 2], [2, 1, 2], [2, 1, 5], [1, 2, 5], [2, 3, 5]]
PCKET 7 1 3 11 10 0 [[2, 2, 4], [1, 2, 2], [2, 1, 2], [2, 1, 5], [3, 2, 5], [2, 2, 2]]
PCKET 7 1 3 11 10 2 [[2, 2, 4], [1, 2, 2], [2, 1, 2], [2, 1, 5], [3, 2, 5], [3, 2, 2]]
PCKET 7 1 3 11 10 4 [[2, 2, 4], [1, 2, 2], [2, 1, 2], [2, 1, 5], [3, 2, 5], [2, 3, 2]]
PCKET 7 1 3 11 10 5 [[2, 2, 4], [1, 2, 2], [2, 1, 2], [2, 1, 5], [3, 2, 5], [2, 2, 1]]
PCKET 7 1 3 11 10 6 [[2, 2, 4], [1, 2, 2], [2, 1, 2], [2, 1, 5], [3, 2, 5], [2, 2, 3]]
PCKET 7 1 3 11 10 8 [[2, 2, 4], [1, 2, 2], [2, 1, 2], [2, 1, 5], [3, 2, 5], [2, 2, 6]]
PCKET 7 1 3 11 10 9 [[2, 2, 4], [1, 2, 2], [2, 1, 2], [2, 1, 5], [3, 2, 5], [1, 2, 5]]
PCKET 7 1 3 11 10 12 [[2, 2, 4], [1, 2, 2], [2, 1, 2], [2, 1, 5], [3, 2, 5], [2, 3, 5]]
PCKET 7 1 3 11 12 0 [[2, 2, 4], [1, 2, 2], [2, 1, 2], [2, 1, 5], [2, 3, 5], [2, 2, 2]]
PCKET 7 1 3 11 12 2 [[2, 2, 4], [1, 2, 2], [2, 1, 2], [2, 1, 5], [2, 3, 5], [3, 2, 2]]
PCKET 7 1 3 11 12 4 [[2, 2, 4], [1, 2, 2], [2, 1, 2], [2, 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



PCKET 11 2 6 1 9 4 [[2, 1, 5], [3, 2, 2], [2, 2, 3], [1, 2, 2], [1, 2, 5], [2, 3, 2]]
PCKET 11 2 6 1 9 5 [[2, 1, 5], [3, 2, 2], [2, 2, 3], [1, 2, 2], [1, 2, 5], [2, 2, 1]]
PCKET 11 2 6 1 9 7 [[2, 1, 5], [3, 2, 2], [2, 2, 3], [1, 2, 2], [1, 2, 5], [2, 2, 4]]
PCKET 11 2 6 1 9 8 [[2, 1, 5], [3, 2, 2], [2, 2, 3], [1, 2, 2], [1, 2, 5], [2, 2, 6]]
PCKET 11 2 6 1 9 10 [[2, 1, 5], [3, 2, 2], [2, 2, 3], [1, 2, 2], [1, 2, 5], [3, 2, 5]]
PCKET 11 2 6 1 9 12 [[2, 1, 5], [3, 2, 2], [2, 2, 3], [1, 2, 2], [1, 2, 5], [2, 3, 5]]
PCKET 11 2 6 1 10 0 [[2, 1, 5], [3, 2, 2], [2, 2, 3], [1, 2, 2], [3, 2, 5], [2, 2, 2]]
PCKET 11 2 6 1 10 3 [[2, 1, 5], [3, 2, 2], [2, 2, 3], [1, 2, 2], [3, 2, 5], [2, 1, 2]]
PCKET 11 2 6 1 10 4 [[2, 1, 5], [3, 2, 2], [2, 2, 3], [1, 2, 2], [3, 2, 5], [2, 3, 2]]
PCKET 11 2 6 1 10 5 [[2, 1, 5], [3, 2, 2], [2, 2, 3], [1, 2, 2], [3, 2, 5], [2, 2, 1]]
PCKET 11 2 6 1 10 7 [[2, 1, 5], [3, 2, 2], [2, 2, 3], [1, 2, 2], [3, 2, 5], [2, 2, 4]]
PCKET 11 2 6 1 10 8 [[2, 1, 5], [3, 2, 2], [2, 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



# Day 19

In [107]:
input = get_input(19)
test = """Blueprint 1:  Each ore robot costs 4 ore.  Each clay robot costs 2 ore.  Each obsidian robot costs 3 ore and 14 clay.  Each geode robot costs 2 ore and 7 obsidian.
Blueprint 2:  Each ore robot costs 2 ore.  Each clay robot costs 3 ore.  Each obsidian robot costs 3 ore and 8 clay.  Each geode robot costs 3 ore and 12 obsidian.""".split('\n')

def is_int(x):
    try:
        int(x)
    except:
        return False
    return True

def foo(data):
    bps = []
    for row in data:
        bp = [int(x) for x in row.split() if is_int(x)]
        # ore, clay=ore, obs=ore/clay, geo=ore/obs
        bps.append([bp[0], bp[1], bp[2:4], bp[4:]])
    
    q = 0
    for idx,bp in enumerate(bps):
        print(idx+1,bp)
        ore = clay = obs = geo = 0
        more = 1
        mclay = mobs = mgeo = 0
        bore, bclay, bobs, bgeo = bp
        for i in range(24):
            try:
                next_geo = max((bgeo[0]-ore)//more+1, (bgeo[1]-obs)//mobs+1)
            except ZeroDivisionError:
                next_geo = 100
            try:
                next_next_geo = max((bgeo[0]-ore+bobs[0])//more+1, (bgeo[1]-obs)//(mobs+1)+1)
            except ZeroDivisionError:
                next_next_geo = 99
            try:
                next_obs = max((bobs[0]-ore)//more+1, (bobs[1]-clay)//mclay+1)
            except ZeroDivisionError:
                next_obs = 100
            try:
                next_next_obs = max((bobs[0]-ore+bclay)//more+1, (bobs[1]-clay)//(mclay+1)+1)
            except ZeroDivisionError:
                next_next_obs = 99
            try:
                next_clay = (bclay-clay)//more+1
            except ZeroDivisionError:
                next_clay = 100
            try:
                next_next_clay = (bclay-clay)//(more+1)+1
            except ZeroDivisionError:
                next_next_clay = 99
            action = ''
            if ore >= bgeo[0] and obs >= bgeo[1]:
                # Build a geo
                action = 'build GEO'
                ore += more
                clay += mclay
                obs += mobs
                geo += mgeo
                
                ore -= bgeo[0]
                obs -= bgeo[1]
                mgeo += 1
            elif next_geo < next_next_geo:
                # Wait to build geo next
                action = 'nothing (await geo)'
                ore += more
                clay += mclay
                obs += mobs
                geo += mgeo
            elif ore >= bobs[0] and clay >= bobs[1]:
                # Build obsidan
                action = 'build OBS'
                ore += more
                clay += mclay
                obs += mobs
                geo += mgeo
                
                ore -= bobs[0]
                clay -= bobs[1]
                mobs += 1
            elif next_obs < next_next_obs:
                # Wait to build obsidan next
                action = 'nothing (await obs)'
                ore += more
                clay += mclay
                obs += mobs
                geo += mgeo
            elif ore >= bclay:
                action = 'build CLAY'
                ore += more
                clay += mclay
                obs += mobs
                geo += mgeo
                
                ore -= bclay
                mclay += 1
            elif next_clay <= next_next_clay:
                # Wait to build clay next
                action = 'nothing (await clay)'
                ore += more
                clay += mclay
                obs += mobs
                geo += mgeo
            elif ore >=bore:
                action = 'build ORE'
                ore += more
                clay += mclay
                obs += mobs
                geo += mgeo
                
                ore -= bore
                more += 1
            else:
                action = 'nothing'
                ore += more
                clay += mclay
                obs += mobs
                geo += mgeo
            print(i+1,more,ore,mclay,clay,mobs,obs,mgeo,geo,action)
        print(idx+1,geo)
        q += (idx+1) * geo
                
            
    return q

output(foo(test))
#output(foo(input))

1 [4, 2, [3, 14], [2, 7]]
1 1 1 0 0 0 0 0 0 nothing
2 1 2 0 0 0 0 0 0 nothing
3 1 1 1 0 0 0 0 0 build CLAY
4 1 2 1 1 0 0 0 0 nothing
5 1 1 2 2 0 0 0 0 build CLAY
6 1 2 2 4 0 0 0 0 nothing (await clay)
7 1 1 3 6 0 0 0 0 build CLAY
8 1 2 3 9 0 0 0 0 nothing (await obs)
9 1 3 3 12 0 0 0 0 nothing (await obs)
10 1 4 3 15 0 0 0 0 nothing (await obs)
11 1 2 3 4 1 0 0 0 build OBS
12 1 1 4 7 1 1 0 0 build CLAY
13 1 2 4 11 1 2 0 0 nothing (await obs)
14 1 3 4 15 1 3 0 0 nothing (await obs)
15 1 1 4 5 2 4 0 0 build OBS
16 1 2 4 9 2 6 0 0 nothing (await geo)
17 1 3 4 13 2 8 0 0 nothing (await geo)
18 1 2 4 17 2 3 1 0 build GEO
19 1 3 4 21 2 5 1 1 nothing (await geo)
20 1 4 4 25 2 7 1 2 nothing (await geo)
21 1 3 4 29 2 2 2 3 build GEO
22 1 1 4 19 3 4 2 5 build OBS
23 1 2 4 23 3 7 2 7 nothing (await geo)
24 1 1 4 27 3 3 3 9 build GEO
1 9
2 [2, 3, [3, 8], [3, 12]]
1 1 1 0 0 0 0 0 0 nothing
2 1 2 0 0 0 0 0 0 nothing
3 2 1 0 0 0 0 0 0 build ORE
4 2 3 0 0 0 0 0 0 nothing (await clay)
5 2 2 1 0 0 0 0 0

# Day 20

In [34]:
input = get_input(20)
test = """1
2
-3
3
-2
0
4""".split('\n')

class Link(object):
    def __init__(self, val):
        self.val = val
        self.next = None
        self.prev = None

def gen_list(data, mult=1):
    last = None
    first = None
    nodes = []
    zero = None
    for x in data:
        link = Link(int(x) * mult)
        if last is not None:
            last.next = link
            link.prev = last
        else:
            first = link
        last = link
        nodes.append(link)
        if x == '0':
            zero = link
    last.next = first
    first.prev = last
    return nodes, zero

def get_vals(node, num):
    a = []
    for i in range(num):
        a.append(node.val)
        node = node.next
    return a

def mix(data, num_mix=1, mult=1):    
    nodes, zero = gen_list(data, mult)
    for _ in range(num_mix):
        #print(get_vals(zero, len(nodes)))
        for node in nodes:
            for i in range(abs(node.val) % (len(nodes)-1)):
                p = node.prev
                n = node.next
                if node.val > 0:
                    p.next = n
                    n.prev = p
                    node.prev = n
                    node.next = n.next
                    n.next = node
                    node.next.prev = node
                else:
                    p.next = n
                    n.prev = p
                    node.prev = p.prev
                    node.next = p
                    p.prev = node
                    node.prev.next = node
                #print(get_vals(zero, len(nodes)))
            
    a = get_vals(zero, len(nodes))
    return sum([a[i%len(a)] for i in [1000,2000,3000]])

output(mix(test))
#output(mix(test,2,2))
output(mix(test, 10, 811589153))
output(mix(input))
output(mix(input, 10, 811589153))

3
1623178306
8372
7865110481723


# Day 21

In [19]:
input = get_input(21)
test = """root: pppw + sjmn
dbpl: 5
cczh: sllz + lgvd
zczc: 2
ptdq: humn - dvpt
dvpt: 3
lfqf: 4
humn: 5
ljgn: 2
sjmn: drzm * dbpl
sllz: 4
pppw: cczh / lfqf
lgvd: ljgn * ptdq
drzm: hmdt - zczc
hmdt: 32""".split('\n')

def part_one(data):
    for i in range(1000):
        for row in data:
            monkey, eq = row.split(':')
            try:
                exec(f"{monkey} = {eq}")
                return int(eval('root'))
            except Exception as e:
                #print(e)
                pass
            
def get_root(data, humn):
    for i in range(1000):
        for row in data:
            monkey, eq = row.split(':')
            if monkey == 'root':
                eq = eq.replace('+', '==')
            elif monkey == 'humn':
                continue
            try:
                exec(f"{monkey} = {eq}")
                #print(f"{monkey} = {eq}")
                if len(data) < 20:
                    print(humn, eval('root'), eval('humn'), eval('pppw'), eval('sjmn'))
                else:
                    print(humn, eval('root'), eval('humn'), eval('wvvv'), eval('whqc'), eval('wvvv - whqc'))

                return eval('root')
            except Exception as e:
                #print(e)
                pass

def part_two(data):
    #for i in range(500):
    for i in range(20):
        if get_root(data, 3000000000000*i):
            return i


def get_root(data, humn):
    for i in range(1000):
        for row in data:
            monkey, eq = row.split(':')
            if monkey == 'root':
                eq = eq.replace('+', '==')
            elif monkey == 'humn':
                continue
            try:
                __loader__
                exec(f"{monkey} = {eq}")
                #print(f"{monkey} = {eq}")
                if len(data) < 20:
                    return eval('pppw - sjmn')
                else:
                    return eval('wvvv - whqc')

                return eval('root')
            except Exception as e:
                #print(e)
                pass

def part_two(data):
    humn = 1
    while get_root(data, humn) > 0:
        humn *= 10
        #print(humn)
    humn //= 10
    print(humn)
    
    digits = len(str(humn))
    for i in range(digits+1):
        inc = 10**(digits-i)
        while get_root(data, humn) > 0:
            humn += inc
            #print(humn)
        humn -= inc
        print(humn)
    
    return humn+1

output(part_one(test))
#output(part_one(input))
#output(part_two(test))
output(part_two(input))
#output(get_root(input, 3469704905529)) # manual trial/error!  3469704905529  

152
1000000000000
1000000000000
3000000000000
3400000000000
3460000000000
3469000000000
3469700000000
3469700000000
3469704000000
3469704900000
3469704900000


KeyboardInterrupt: 

# Day 22

In [55]:
input = get_input(22, '\n', None)
test = """        ...#    
        .#..    
        #...    
        ....    
...#.......#    
........#...    
..#....#....    
..........#.    
        ...#....
        .....#..
        .#......
        ......#.

10R5L5R10L4R5L5""".split('\n')

def other_side(x,y,d,grid):
    gx = np.where(grid[y,:]>= 0)[0]
    gy = np.where(grid[:,x]>=0)[0]
    return {
        0: (gx[0], y),
        1: (x, gy[0]),
        2: (gx[-1], y),
        3: (x, gy[-1])
    }[d]
    
def do_move(x,y,d,num,grid):
    f = lambda x,y,d: {0:(x+1,y),1:(x,y+1),2:(x-1,y),3:(x,y-1)}[d]
    for i in range(num):
        x1,y1 = f(x,y,d)
        if x1 < 0 or x1 == grid.shape[1] or y1 < 0 or y1 == grid.shape[0]:
            val = other_side(x,y,d,grid)
        else:
            val = grid[y1][x1]
            
        if val == 0:
            x = x1
            y = y1
        elif val == 1:
            return x,y
        else:
            x1,y1 = other_side(x,y,d,grid)
            val = grid[y1][x1]
            if val == 0:
                x = x1
                y = y1
            elif val == 1:
                return x,y
            else:
                raise
    return x,y
        
def other_side_cube(x,y,d,grid):
    x,y = {0:(x+1,y),1:(x,y+1),2:(x-1,y),3:(x,y-1)}[d]
    if val == -1:
        pass
    else:
        return x,y,d,val

    
def do_move_cube(x,y,d,num,grid):
    for i in range(num):
        x1,y1,d1,val = next_cube(x,y,d,grid)
        if val == 0:
            x = x1
            y = y1
            d = d1
        elif val == 1:
            return x,y,d
        else:
            raise
    return x,y,d

def foo(data, cube=False):
    grid = []
    spaces = {' ':-1, '.':0, '#':1}
    width = 0
    done = False
    for row in data:
        if row:
            if done:
                moves_list = row
                break
                
            if width == 0:
                width = len(row)
            elif len(row) < width:
                row += " " * (width - len(row))
            else:
                assert len(row) == width
            
            grid.append([spaces[x] for x in row])
        else:
            done = True
    grid = np.asarray(grid,np.int8)
    
    moves = []
    move = ''
    for m in moves_list:
        if m in ['L','R']:
            moves.append(int(move))
            moves.append(m)
            move = ''
        else:
            move += m
    if m not in ['L','R']:
        moves.append(int(move))
    
    x = np.where(grid[0,:]==0)[0][0]
    y = 0
    d = 0
    for m in moves:
        if m == 'L':
            d = (d-1) % 4
        elif m == 'R':
            d = (d+1) % 4
        elif cube:
            x,y,d = do_move_cube(x,y,d,m,grid)
        else:
            x,y = do_move(x,y,d,m,grid)
    
    return 1000*(y+1) + 4*(x+1) + d

output(foo(test))
output(foo(input))

6032
30552


# Day 23

In [87]:
f = lambda x: x.replace('.','0').replace('#','1').strip()
input = as_ints(get_input(23, f=f))
test = """....#..
..###.#
#...#.#
.#...##
#.###..
##.#.##
.#..#..""".split('\n')

test = as_ints([f(x) for x in test])

fn = lambda k: np.max(k[0,:])
fs = lambda k: np.max(k[2,:])
fw = lambda k: np.max(k[:,0])
fe = lambda k: np.max(k[:,2])
funcs = [fn, fs, fw, fe]

iN = lambda x,y: (y-1,x)
iS = lambda x,y: (y+1,x)
iW = lambda x,y: (y,x-1)
iE = lambda x,y: (y,x+1)
idxs = [iN, iS, iW, iE]

def move(a,b,x,y,r,moves):
    k = a[y-1:y+2,x-1:x+2]
    if np.sum(k) == 1:
        return # no move
    
    for i in range(4):
        if funcs[(r+i)%4](k) == 0:
            y0, x0 = idxs[(r+i)%4](x,y)
            #print(f"MOVE {x},{y} => {x0},{y0}")
            if (x0,y0) in moves:
                b[y0,x0] = 0
                b[moves[(x0,y0)]] = 1
            else:
                moves[(x0,y0)] = (y,x)
                b[y,x] = 0
                b[y0,x0] += 1
            break
    
def foo(data, lim=10):
    h, w = data.shape
    b = np.zeros((h*3,w*3), np.int8)
    b[h:2*h,w:2*w] = data
    for r in range(lim):
        moves = {}
        a = b.copy()
#        print(f"ROUND {r}")
#        print(b[6:12,6:12])
#        print('----------------')
        sq = np.where(a==1)
        for y, x in zip(sq[0], sq[1]):
                move(a, b, x, y, r, moves)
#                print(b[6:12,6:12])
#                print('----------------')
#        print(b[6:12,6:12])
        if np.array_equal(a,b):
            return f"No move at {r+1}"
    sq = np.where(b==1)
    sq = b[min(sq[0]):max(sq[0])+1, min(sq[1]):max(sq[1])+1]
    shape = sq.shape
    return shape[0] * shape[1] - np.count_nonzero(sq)
        

output(foo(test))
output(foo(input))
output(foo(test, 30))
output(foo(input, 1000))

110
4146
No move at 20
No move at 957


# Day 24

In [141]:
input = get_input(24)
test = """#.######
#>>.<^<#
#.<..<<#
#>v.><>#
#<^v^^>#
######.#""".split('\n')

def update(this, that):
    if this == 0:
        return that
    return int(str(this) + str(that))

def next_grid(grid):
    h, w = grid.shape
    out = np.zeros(grid.shape, np.int32)
    Y, X = np.where(grid > 0)
    for y, x in zip(Y, X):
        c = str(grid[y,x])
        if '1' in c:
            if x == w-1:
                x = -1
            d = out[y,x+1]
            out[y,x+1] = update(d,1)            
        if '2' in c:
            if y == h-1:
                y = -1
            d = out[y+1,x]
            out[y+1,x] = update(d,2)
        if '3' in c:
            if x == 0:
                x = w
            d = out[y,x-1]
            out[y,x-1] = update(d,3)
        if '4' in c:
            if y == 0:
                y = h
            d = out[y-1,x]
            out[y-1,x] = update(d,4)
    return out

def get_moves(grid, c0, start):
    moves = []
    h, w = grid.shape
    if c0 is None:
        if grid[start] == 0:
            moves.append(start)
        moves.append(None)
        return moves
    
    if c0 == start:
        moves.append(None)
    
    y0, x0 = c0
    for c in ((y0,x0), (y0-1,x0), (y0+1,x0), (y0,x0-1), (y0,x0+1)):
        y, x = c
        if x < 0 or y < 0 or x == w or y == h:
            continue
        if grid[c] == 0:
            moves.append(c)
    return moves

def find_path(grid, start, end):
    coords = None
    for r in range(1, 10000):
        #print(r,coords)
        #print(f"ROUND {r}")
        #print(grid)
        #print('----------')
        grid = next_grid(grid)
        if coords is None:
            if grid[start] == 0:
                coords = [start]
            continue
        
        new_coords = []
        for c in coords:
            for m in get_moves(grid, c, start):
                if m == end:
                    return r+1, next_grid(grid)
                if m not in new_coords:
                    new_coords.append(m)
        coords = new_coords

def blizzard(data, there_and_back=False):
    h = len(data)
    w = len(data[0])
    grid = np.zeros((h-2,w-2), np.int32)
    for y in range(1,h-1):
        for x in range(1,w-1):
            c = data[y][x]
            if c == '.':
                d = 0
            elif c == '>':
                d = 1
            elif c == 'v':
                d = 2
            elif c == '<':
                d = 3
            elif c == '^':
                d = 4
            grid[y-1][x-1] = d
    
    r, grid = find_path(grid, (0,0), (h-3,w-3))
    #print(r,grid)
    if there_and_back:
        r2, grid = find_path(grid, (h-3,w-3), (0,0))
        r3, grid = find_path(grid, (0,0), (h-3,w-3))
        r = r + r2 + r3
    
    return r
    
    


output(blizzard(test))
output(blizzard(input))
output(blizzard(test, True))
output(blizzard(input, True))

18
343
54
960


# Day 25

In [20]:
input = get_input(25)
test = """1=-0-2
12111
2=0=
21
2=01
111
20012
112
1=-1=
1-12
12
1=
122""".split('\n')

def snafu_to_dec(s):
    d = 0
    for i in range(-1, -len(s)-1, -1):
        c = s[i]
        if c in ('0','1','2'):
            pass
        elif c == '-':
            c = -1
        elif c == '=':
            c = -2
        else:
            raise
        d += int(c) * 5**(abs(i)-1)
    return d

def dec_to_snafu(d):
    s = ''
    exp = 0
    while d // 5**exp > 0:
        exp += 1
    
    while exp > 0:
        exp -= 1
        r = d // 5**exp
        s += str(r)
        d -= r * 5**exp
    return fix_snafu(s)

def fix_snafu(s):
    #print(s)
    for i in range(len(s)):
        c = s[i]
        if c in ('0','1','2','-','='):
            continue
        
        if i == 0:
            s = '0' + s
            i = 1
        
        c = {'3':'=', '4':'-'}[c]
        b = {'0':'1', '1':'2', '2':'3', '-':'0', '=':'-'}[s[i-1]]
        
        return fix_snafu(s[:i-1] + b + c + s[i+1:])
    return s

def sum_snafu(data):
    d = 0
    for row in data:
        d += snafu_to_dec(row)
    return dec_to_snafu(d)

output(sum_snafu(test))
output(sum_snafu(input))

2=-1=0
20=212=1-12=200=00-1
